<a href="https://colab.research.google.com/github/IbrahemElsherif/kaggle/blob/main/Finetuning.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from google.colab import drive
drive.mount('/gdrive')

Drive already mounted at /gdrive; to attempt to forcibly remount, call drive.mount("/gdrive", force_remount=True).


## Setup


In [2]:
!pip install -qU transformers==4.48.3 datasets==3.2.0 optimum==1.24.0
!pip install -qU openai==1.61.0 wand
!pip install -qU json-repair==0.29.1
!pip install -qU faker==35.2.0
!pip install -qU vllm==0.7.2


Usage:   
  pip3 install [options] <requirement specifier> [package-index-options] ...
  pip3 install [options] -r <requirements file> [package-index-options] ...
  pip3 install [options] [-e] <vcs project url> ...
  pip3 install [options] [-e] <local project path> ...
  pip3 install [options] <archive url/path> ...

no such option: -u


In [3]:
!git clone --depth 1 https://github.com/hiyouga/LLaMA-Factory.git
!cd LLaMA-Factory && pip install -e ".[torch,metrics]" --no-build-isolation

fatal: destination path 'LLaMA-Factory' already exists and is not an empty directory.
Obtaining file:///content/LLaMA-Factory
  Checking if build backend supports build_editable ... done
  Preparing editable metadata (pyproject.toml) ... done
  Using cached transformers-4.57.1-py3-none-any.whl.metadata (43 kB)
  Using cached tokenizers-0.22.1-cp39-abi3-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (6.8 kB)
Using cached transformers-4.57.1-py3-none-any.whl (12.0 MB)
Using cached tokenizers-0.22.1-cp39-abi3-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (3.3 MB)
  Building editable for llamafactory (pyproject.toml) ... done
  Created wheel for llamafactory: filename=llamafactory-0.9.4.dev0-0.editable-py3-none-any.whl size=28499 sha256=9d0582b29cfbeded3765bce2f184bdb9216fd820f4264681194c0311dd7aff27
  Stored in directory: /tmp/pip-ephem-wheel-cache-klof5ia6/wheels/68/8b/5e/52f9888e6a91a2651260d603137c052b925af896da6e32a3f7
Successfully built llamafactory
  Attempting uninstall: 

In [3]:
from google.colab import userdata
import wandb

wandb.login(key=userdata.get('WANDB_ACCES'))
hf_token = userdata.get("HF_ACCESS_TOKEN")
# !huggingface-cli login --token {hf_token}
!hf auth login --token {hf_token}

wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: ebrahem-hesham-ahmed (ebrahem-hesham-ahmed-ibrahem-elsherif) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


The token has not been saved to the git credentials helper. Pass `add_to_git_credential=True` in this function directly or `--add-to-git-credential` if using via `hf`CLI if you want to set the git credential as well.
Token is valid (permission: fineGrained).
The token `colab` has been saved to /root/.cache/huggingface/stored_tokens
Your token has been saved to /root/.cache/huggingface/token
Login successful.
The current active token is: `colab`


## Imports

In [4]:
import os
import json
import requests
from os.path import join
import random
from tqdm.auto import tqdm

from pydantic import BaseModel, Field
from typing import List, Optional, Literal
from datetime import datetime

import json_repair

from transformers import AutoModelForCausalLM, AutoTokenizer, BitsAndBytesConfig
import torch

data_dir = "/gdrive/MyDrive/Colab_Notebooks/Finetuning"
base_model_id = "Qwen/Qwen2.5-1.5B-Instruct"

device = "cuda"
dtype = None

def parse_json(text):
  try:
    return json_repair.loads(text)
  except:
    return None

## Tasks

In [ ]:
story = """
ذكرت مجلة فوربس أن العائلة تلعب دورا محوريا في تشكيل علاقة الأفراد بالمال،
 حيث تتأثر هذه العلاقة بأنماط السلوك المالي المتوارثة عبر الأجيال.

التقرير الذي يستند إلى أبحاث الأستاذ الجامعي شاين إنيت حول
الرفاه المالي يوضح أن لكل شخص "شخصية مالية" تتحدد وفقا لطريقة
 تفاعله مع المال، والتي تتأثر بشكل مباشر بتربية الأسرة وتجارب الطفولة.

 الأبعاد الثلاثة للعلاقة بالمال
بحسب الدراسة، هناك ثلاثة أبعاد رئيسية تشكّل علاقتنا بالمال:

الاكتساب (A): يميل الأفراد الذين ينتمون لهذا
 البعد إلى اعتبار المال سلعة قابلة للجمع، حيث يرون
في تحقيق الثروة هدفا بحد ذاته. والجانب السلبي لهذا
 النمط هو إمكانية التحول إلى هوس بالثروة أو العكس،
 أي رفض تام لاكتساب المال باعتباره مصدرا للفساد.

الاستخدام (U): يرى هؤلاء الأشخاص المال أداة للتمتع بالحياة، حيث يربطون قيمته بقدرته على توفير
المتعة والراحة. ومع ذلك، قد يصبح
البعض مدمنا على الإنفاق، في حين يتجه آخرون إلى التقشف المفرط خوفا من المستقبل.

الإدارة (M): أصحاب هذا النمط يعتبرون المال مسؤولية تتطلب التخطيط الدقيق. لكن في بعض الحالات،
 قد يتحول الأمر إلى هوس مفرط بإدارة الإنفاق، مما يؤثر سلبا على العلاقات الشخصية.

 كيف تؤثر العائلة على علاقتنا بالمال؟
يشير التقرير إلى أن التجارب الأسرية تلعب دورا رئيسيا في تحديد
 "الشخصية المالية" لكل فرد، على سبيل المثال، إذا كان أحد الوالدين يعتمد على المال
كمكافأة للسلوك الجيد، فقد يتبنى الطفل لاحقا النمط نفسه في حياته البالغة.

لتحليل هذه التأثيرات بشكل دقيق، طورت رابطة العلاج المالي
(Financial Therapy Association) أداة تسمى مخطط الجينوم المالي (Money Genogram)،
وهو نموذج يُستخدم لتحديد الأنماط المالية داخل العائلة.

تتضمن هذه الأداة:

رسم شجرة عائلية.
تصنيف أفراد العائلة وفقا للأبعاد الثلاثة للعلاقة بالمال (A ،U ،M).
تحديد ما إذا كان السلوك المالي لكل فرد صحيا (+) أو غير صحي (-).
على سبيل المثال، إذا نشأ شخص في عائلة
اعتادت على الإنفاق المفرط، فقد يكون لديه ميل قوي إلى اتباع النمط نفسه،
 أو العكس تماما، حيث يصبح مقتصدا بشكل مبالغ فيه كرد فعل نفسي.
"""

In [5]:
## Test on new data
story = """
كتب هاني عبد النبي
كشفت الإحصائيات الرسمية الصادرة عن الاتحاد الأوروبي لكرة القدم "يويفا" أن النجم المصري محمد صلاح، جناح ليفربول الإنجليزي، دخل قائمة أسرع 10 لاعبين في دوري أبطال أوروبا هذا الموسم، بعد أن سجل سرعة قصوى بلغت 34.3 كيلومترًا في الساعة.

اينتراخت ضد ليفربول
وتصدر القائمة لويس أوبيندا لاعب يوفنتوس بسرعة 36.2 كم/ساعة، متقدمًا على الجابوني بيير إيمريك أوباميانج نجم مارسيليا (35.8 كم/ساعة)، فيما جاء الهولندي جيريمي فريمبونج لاعب ليفربول في المركز الثالث بسرعة 35.6 كم/ساعة.

وعانى محمد صلاح من تراجع على مستوى تسجيل الأهداف هذا الموسم عن الأعوام الماضية ما ساهم في تلقيه عددًا من الانتقادات بالرغم من تصدره الأرقام في ليفربول.

وأظهرت الاحصائية أن محمد صلاح أسرع لاعب من الدوري الإنجليزي في بطولة دوري أبطال أوروبا، بالإضافة الى نادي ليفربول متفوقًا على جيريمي فيريمبونج.

وفيما يلي ترتيب أسرع لاعبي البطولة حتى الآن:
لويس أوبيندا (يوفنتوس) – 36.2 كم/ساعة

بيير إيمريك أوباميانج (مارسيليا) – 35.8 كم/ساعة

جيريمي فريمبونج (ليفربول) – 35.6 كم/ساعة

كريم أديمي (بوروسيا دورتموند) – 35.4 كم/ساعة

راؤول بيلانوفا (أتالانتا) – 35 كم/ساعة

برادلي باركولا (باريس سان جيرمان) – 35 كم/ساعة

بيدرو نيتو (تشيلسي) – 34.9 كم/ساعة

جيد سيبنز (توتنهام) – 34.5 كم/ساعة

نونو مينديز (باريس سان جيرمان) – 34.4 كم/ساعة

تيموثي ويا (مارسيليا) – 34.3 كم/ساعة

لويد كيلي (يوفنتوس) – 34.3 كم/ساعة

محمد صلاح (ليفربول) – 34.3 كم/ساعة

ماسون جرينوود (مارسيليا) – 34.3 كم/ساعة

"""

## Details Extraction

In [7]:
# # Json
# {
#     "story_title": "",
#     "story_keywords": ["kw1", "kw2"],
#     "story_summary": ["....", '....'],
#     "story_category": "",
#     "story_entities": [
#         {
#             "enitiy_value": "القاهرة",
#             "entity_type": "location"
#         }
#     ]
# }

In [6]:
# Pydantic models
StoryCategory = Literal[
    "politics", "sports", "art", "technology", "economy",
    "health", "entertainment", "science",
    "not_specified"
    ]

EntityType = Literal[
    "person-male", "person-female", "location", "organization", "event", "time",
    "quantity", "money", "product", "law", "disease", "artifact", "not_specified"
    ]

class Entity(BaseModel):
  entity_value: str = Field(..., description="The actual name or value of the entity.")
  entity_type: EntityType = Field(..., description="The type of recognized entity.")

class NewsDetails(BaseModel):
  story_title: str = Field(..., min_length=5, max_length=300,
                           description="A fully informative and SEO optimized title of the story.")
  story_keywords: List[str] = Field(..., min_items=1,
                                    description="Relevant keywords associated with the story.")
  story_summary: List[str] = Field(..., min_items=1, max_items=5,
                                    description="Summarized key points about the story (1-5 points).")
  story_category: StoryCategory = Field(..., description="Category of the news story.")
  story_entities: List[Entity] = Field(..., min_items=1, max_items=10,
                                          description="List of identified entities in the story.")

In [ ]:
# # Exaplanation
# # json.dumps(["السلام عليكم"])
# json.dumps(["السلام عليكم"], ensure_ascii= False)

# NewsDetailsNewsDetails.model_json_schema()

In [7]:
details_extraction_messages = [
    {
        "role": "system",
        "content":"\n".join([ # we use join with lsit of strings to eliminate spaces
            "You are an NLP data paraser.",
            "You will be provided by an Arabic text associated with a Pydantic scheme.",
            "Generate the ouptut in the same story language.",
            "You have to extract JSON details from text according the Pydantic details.",
            "Extract details as mentioned in text.",
            "Do not generate any introduction or conclusion."
        ])
    },
    {"role": "user",
    "content": "\n".join([
        "## Story:",
        story.strip(),
        "",

        "## Pydantics Details:",
        json.dumps( # Transform to json
            NewsDetails.model_json_schema(), ensure_ascii=False # for non-latin language like arabic
        ),
        "",

        "##Story Detials:",
        "```json" # To know the user wants json

    ])}
]

## Translation

In [ ]:
# {
#     "translated_title": "",
#     "translated_content": ""
# }

In [8]:
class TranslatedStory(BaseModel):
    translated_title: str = Field(..., min_length=5, max_length=300,
                                  description="Suggested translated title of the news story.")
    translated_content: str = Field(..., min_length=5,
                                    description="Translated content of the news story.")

targeted_lang = "English"

translation_messages = [
    {
        "role": "system",
        "content": "\n".join([
            "You are a professional translator.",
            "You will be provided by an Arabic text.",
            "You have to translate the text into the `Targeted Language`.",
            "Follow the provided Scheme to generate a JSON",
            "Do not generate any introduction or conclusion."
        ])
    },
    {
        "role": "user",
        "content":  "\n".join([
            "## Story:",
            story.strip(),
            "",

            "## Pydantic Details:",
            json.dumps( TranslatedStory.model_json_schema(), ensure_ascii=False ),
            "",

            "## Targeted Language:",
            targeted_lang,
            "",

            "## Translated Story:",
            "```json"

        ])
    }
]

## Evaluation

In [13]:
model = AutoModelForCausalLM.from_pretrained(
    base_model_id,
    device_map="auto",
    torch_dtype=dtype # To control quantization
)

tokenizer = AutoTokenizer.from_pretrained(base_model_id)


/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/660 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/3.09G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/242 [00:00<?, ?B/s]

tokenizer_config.json: 0.00B [00:00, ?B/s]

vocab.json: 0.00B [00:00, ?B/s]

merges.txt: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

In [14]:
model

Qwen2ForCausalLM(
  (model): Qwen2Model(
    (embed_tokens): Embedding(151936, 1536)
    (layers): ModuleList(
      (0-27): 28 x Qwen2DecoderLayer(
        (self_attn): Qwen2Attention(
          (q_proj): Linear(in_features=1536, out_features=1536, bias=True)
          (k_proj): Linear(in_features=1536, out_features=256, bias=True)
          (v_proj): Linear(in_features=1536, out_features=256, bias=True)
          (o_proj): Linear(in_features=1536, out_features=1536, bias=False)
        )
        (mlp): Qwen2MLP(
          (gate_proj): Linear(in_features=1536, out_features=8960, bias=False)
          (up_proj): Linear(in_features=1536, out_features=8960, bias=False)
          (down_proj): Linear(in_features=8960, out_features=1536, bias=False)
          (act_fn): SiLUActivation()
        )
        (input_layernorm): Qwen2RMSNorm((1536,), eps=1e-06)
        (post_attention_layernorm): Qwen2RMSNorm((1536,), eps=1e-06)
      )
    )
    (norm): Qwen2RMSNorm((1536,), eps=1e-06)
    (rotar

In [15]:
text = tokenizer.apply_chat_template(
    details_extraction_messages,
    tokenize=False,
    add_generation_prompt=True)
text

'<|im_start|>system\nYou are an NLP data paraser.\nYou will be provided by an Arabic text associated with a Pydantic scheme.\nGenerate the ouptut in the same story language.\nYou have to extract JSON details from text according the Pydantic details.\nExtract details as mentioned in text.\nDo not generate any introduction or conclusion.<|im_end|>\n<|im_start|>user\n## Story:\nذكرت مجلة فوربس أن العائلة تلعب دورا محوريا في تشكيل علاقة الأفراد بالمال،\n حيث تتأثر هذه العلاقة بأنماط السلوك المالي المتوارثة عبر الأجيال.\n\nالتقرير الذي يستند إلى أبحاث الأستاذ الجامعي شاين إنيت حول\nالرفاه المالي يوضح أن لكل شخص "شخصية مالية" تتحدد وفقا لطريقة\n تفاعله مع المال، والتي تتأثر بشكل مباشر بتربية الأسرة وتجارب الطفولة.\n\n الأبعاد الثلاثة للعلاقة بالمال\nبحسب الدراسة، هناك ثلاثة أبعاد رئيسية تشكّل علاقتنا بالمال:\n\nالاكتساب (A): يميل الأفراد الذين ينتمون لهذا\n البعد إلى اعتبار المال سلعة قابلة للجمع، حيث يرون\nفي تحقيق الثروة هدفا بحد ذاته. والجانب السلبي لهذا\n النمط هو إمكانية التحول إلى هوس 

In [16]:
text = tokenizer.apply_chat_template(
    details_extraction_messages,
    tokenize=False,
    add_generation_prompt=True
)

model_inputs = tokenizer([text], return_tensors="pt").to(device) # run the tekonizer

generate_ids = model.generate(
    model_inputs.input_ids,
    max_new_tokens=200,
    do_sample=False, top_k=None, temperature=None, top_p=None # For sampling
)

generated_ids = [
    output_ids[len(input_ids):] # start from the start of the output ids
    for input_ids, output_ids in zip(model_inputs.input_ids, generate_ids)

]

response = tokenizer.batch_decode(generated_ids, skip_special_tokens=True)[0]


The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.


In [15]:
print(response)

{
  "story_title": "How Family Influences Financial Behavior",
  "story_keywords": [
    "family influence",
    "financial behavior",
    "moneymaking",
    "money management",
    "wealth building"
  ],
  "story_summary": [
    "Family plays a crucial role in shaping individuals' financial relationships.",
    "Individuals inherit certain financial behaviors from their families."
  ],
  "story_category": "economy",
  "story_entities": [
    {
      "entity_value": "Forbes Magazine",
      "entity_type": "organization"
    },
    {
      "entity_value": "Shain Enit",
      "entity_type": "person-female"
    },
    {
      "entity_value": "Financial Therapy Association",
      "entity_type": "organization"
    }
  ]
}


In [17]:
text = tokenizer.apply_chat_template(
    translation_messages,
    tokenize=False,
    add_generation_prompt=True)

In [18]:
text = tokenizer.apply_chat_template(
    translation_messages,
    tokenize=False,
    add_generation_prompt=True
)

model_inputs = tokenizer([text], return_tensors="pt").to(device)

generated_ids = model.generate(
    model_inputs.input_ids,
    max_new_tokens=1024,
    do_sample=False, top_k=None, temperature=None, top_p=None,
)

generated_ids = [
    output_ids[len(input_ids):]
    for input_ids, output_ids in zip(model_inputs.input_ids, generated_ids)
]

response = tokenizer.batch_decode(generated_ids, skip_special_tokens=True)[0]
print(response)

{
  "translated_title": "Forbes Magazine Reveals Family Plays a Central Role in Forming Individuals' Financial Relationships",
  "translated_content": "According to Forbes magazine, family plays a crucial role in shaping individuals' financial relationships, as these relationships are influenced by inherited behavioral patterns across generations."
}


## Evaluate OpenAI

In [20]:
from openai import OpenAI

openai_client = OpenAI(
    api_key=userdata.get("OPENAI_API_KEY")
)

openai_model_id = "gpt-4o-mini"

In [21]:
chat_completion = openai_client.chat.completions.create(
    model=openai_model_id,
    messages=details_extraction_messages,
    temperature=0.2
)

print(chat_completion.choices[0].message.content)

{
  "story_title": "تأثير العائلة على العلاقة بالمال",
  "story_keywords": [
    "العائلة",
    "المال",
    "الشخصية المالية",
    "الرفاه المالي",
    "أنماط السلوك المالي"
  ],
  "story_summary": [
    "العائلة تلعب دورا محوريا في تشكيل علاقة الأفراد بالمال.",
    "هناك ثلاثة أبعاد رئيسية للعلاقة بالمال: الاكتساب، الاستخدام، والإدارة.",
    "التجارب الأسرية تحدد 'الشخصية المالية' لكل فرد.",
    "أداة مخطط الجينوم المالي تُستخدم لتحديد الأنماط المالية داخل العائلة."
  ],
  "story_category": "economy",
  "story_entities": [
    {
      "entity_value": "مجلة فوربس",
      "entity_type": "organization"
    },
    {
      "entity_value": "شاين إنيت",
      "entity_type": "person-male"
    },
    {
      "entity_value": "رابطة العلاج المالي",
      "entity_type": "organization"
    },
    {
      "entity_value": "مخطط الجينوم المالي",
      "entity_type": "artifact"
    }
  ]
}


In [22]:
chat_completion = openai_client.chat.completions.create(
    model=openai_model_id,
    messages=translation_messages,
    temperature=0.2
)

print(chat_completion.choices[0].message.content)

{
  "translated_title": "The Impact of Family on Financial Relationships",
  "translated_content": "Forbes magazine reported that family plays a pivotal role in shaping individuals' relationships with money, as this relationship is influenced by financial behavior patterns passed down through generations.\n\nThe report, based on research by university professor Shane Enright on financial well-being, explains that each person has a 'financial personality' determined by their interaction with money, which is directly affected by family upbringing and childhood experiences.\n\nThe three dimensions of the relationship with money\nAccording to the study, there are three main dimensions that shape our relationship with money:\n\nAcquisition (A): Individuals belonging to this dimension tend to view money as a commodity to be accumulated, seeing wealth attainment as a goal in itself. The downside of this pattern is the potential to develop an obsession with wealth or, conversely, a complete re

## Knowledge Distillation

In [19]:
raw_data_path = join(data_dir, "datasets", "news-sample.jsonl")

raw_data = []

for line in open(raw_data_path):
  if line.strip() == "" :
    continue

  raw_data.append(json.loads(line))

random.Random(101).shuffle(raw_data)

print(f"Raw data: {len(raw_data)}")

Raw data: 2400


In [19]:
raw_data

[{'id': 975,
  'title': 'ما تقدمه فلسطين للعالم.. معرض لآمال وآلام شعبها في باريس',
  'description': 'يواصل المعهد العربي في باريس استقبال زواره في معرض “ما تقدمه فلسطين للعالم” لإطلاعهم على الإرث الثقافي والفني للفلسطينيين، من خلال أعمال فنية لآمالهم، وصور لواقعهم الأليم تحت الاحتلال.',
  'content': 'يواصل المعهد العربي في باريس استقبال زواره في معرض ما تقدمه فلسطين للعالم لإطلاعهم على الإرث الثقافي والفني للفلسطينيين؛ من خلال أعمال فنية لآمالهم وصور لواقعهم الأليم تحت الاحتلال. \n ويرى رئيس المعهد جاك لانغ -الذي أُعيد انتخابه قبل أيام للدورة الرابعة- ما يحدث في غزة حاليا جراء العدوان الإسرائيلي أنه كارثة. \n والمعهد هو مركز ثقافي وواجهة دبلوماسية يديرها لانغ منذ 2013 ويقع على ضفة نهر السين في باريس. \n وأشار لانغ، الذي شغل سابقا منصب وزير الثقافة بفرنسا، إلى أن المعرض هو إهداء للشعب الفلسطيني، ومُدّد ليستقبل مزيدا من الزوار حتى 31 ديسمبركانون الأول الجاري. \n ويضم المعرض، الذي افتُتح أواخر مايوأيار الماضي، حسب لانغ العديد من المعارض الفرعية عن فلسطين وعن غزة بالتحديد، من بينها معرض ا

In [20]:
raw_data[0]['content']

'يواصل المعهد العربي في باريس استقبال زواره في معرض ما تقدمه فلسطين للعالم لإطلاعهم على الإرث الثقافي والفني للفلسطينيين؛ من خلال أعمال فنية لآمالهم وصور لواقعهم الأليم تحت الاحتلال. \n ويرى رئيس المعهد جاك لانغ -الذي أُعيد انتخابه قبل أيام للدورة الرابعة- ما يحدث في غزة حاليا جراء العدوان الإسرائيلي أنه كارثة. \n والمعهد هو مركز ثقافي وواجهة دبلوماسية يديرها لانغ منذ 2013 ويقع على ضفة نهر السين في باريس. \n وأشار لانغ، الذي شغل سابقا منصب وزير الثقافة بفرنسا، إلى أن المعرض هو إهداء للشعب الفلسطيني، ومُدّد ليستقبل مزيدا من الزوار حتى 31 ديسمبركانون الأول الجاري. \n ويضم المعرض، الذي افتُتح أواخر مايوأيار الماضي، حسب لانغ العديد من المعارض الفرعية عن فلسطين وعن غزة بالتحديد، من بينها معرض الصور اليومية عن الحياة في غزة. \n كما يشتمل على معرض الصور الفوتوكرومية القائم على تلوين صور من فلسطين تعود للقرن الـ19. \n ويعرض الفنان الفلسطيني محمد أبو سل عملا فريدا بعنوان مترو غزة، وهو عبارة عن عمل تركيبي متعدد الوسائط، لاقى إعجابا من الزوار. \n ويحضر الشاعر الفلسطيني الراحل محمود درويش من خلال 

In [22]:
# Calculate cost manually
cloud_model_id = "gpt-4o-mini"
price_per_1m_input_tokens = 0.150
price_per_1m_output_tokens = 0.600

prompt_tokens = 0
completion_tokens = 0

save_to = join(data_dir, "datasets", "aaasft.jsonl")
ix = 0 # Initialize ix

for story in tqdm(raw_data):

    sample_details_extraction_messages = [
        {
            "role": "system",
            "content": "\n".join([
                "You are an NLP data paraser.",
                "You will be provided by an Arabic text associated with a Pydantic scheme.",
                "Generate the ouptut in the same story language.",
                "You have to extract JSON details from text according the Pydantic details.",
                "Extract details as mentioned in text.",
                "Do not generate any introduction or conclusion."
            ])
        },
        {
            "role": "user",
            "content": "\n".join([
                "## Story:",
                story['content'].strip(), # to get the content for the raw_data
                "",

                "## Pydantic Details:",
                json.dumps(
                    NewsDetails.model_json_schema(), ensure_ascii=False
                ),
                "",

                "## Story Details:",
                "```json"
            ])
        }
    ]

    response = openai_client.chat.completions.create(
                            messages=sample_details_extraction_messages,
                            model=cloud_model_id,
                            temperature=0.2,
                        )

    if response.choices[0].finish_reason != "stop": # to detect any problem
        prompt_tokens += response.usage.prompt_tokens # to return how many tokens been sent
        continue

    llm_response = response.choices[0].message.content
    llm_resp_dict = parse_json(llm_response)

    if llm_resp_dict is None:
        continue

    # saving to a file
    with open(save_to, "a", encoding="utf-8") as dest:
      dest.write(json.dumps(
      {
          "id": ix,
          "story": story['content'].strip(),
          "task": "Extrat the story details into a JSON.",
          "output_scheme": json.dumps( NewsDetails.model_json_schema(), ensure_ascii=False ),
          "response": llm_resp_dict,
      }, ensure_ascii=False, default= str) + "\n")

    ix +=1
    prompt_tokens += response.usage.prompt_tokens
    completion_tokens += response.usage.completion_tokens

    if (ix % 3) == 0:
      cost_input = (prompt_tokens / 1_000_000) * price_per_1m_input_tokens
      cost_output = (completion_tokens / 1_000_000) * price_per_1m_output_tokens
      total_cost = cost_input + cost_output

      print(f"Iteration {ix}: Total cost = ${total_cost:.4f}")

  0%|          | 0/2400 [00:00<?, ?it/s]

NameError: name 'openai_client' is not defined

In [ ]:
# Calculate cost manually for translation
cloud_model_id = "gpt-4o-mini"
price_per_1m_input_tokens = 0.150
price_per_1m_output_tokens = 0.600

prompt_tokens = 0
completion_tokens = 0

save_to = join(data_dir, "datasets", "sft.jsonl")

ix = 0
for story in tqdm(raw_data):

    for targeted_lang in ["English", "French"]:
        sample_translation_messages = [
            {
                "role": "system",
                "content": "\n".join([
                    "You are a professional translator.",
                    "You will be provided by an Arabic text.",
                    "You have to translate the text into the `Targeted Language`.",
                    "Follow the provided Scheme to generate a JSON",
                    "Do not generate any introduction or conclusion."
                ])
            },
            {
                "role": "user",
                "content": "\n".join([
                    "## Pydantic Details:",
                    json.dumps( TranslatedStory.model_json_schema(), ensure_ascii=False ),
                    "",

                    "## Targeted Language or Dialect:",
                    targeted_lang,
                    "",

                    "## Story:",
                    story['content'].strip(),
                    "",

                    "## Translated Story:",
                    "```json"
                ])
            }
        ]

        response = openai_client.chat.completions.create(
                                messages=sample_translation_messages,
                                model=cloud_model_id,
                                temperature=0.2,
                            )

        if response.choices[0].finish_reason != "stop":
            prompt_tokens += response.usage.prompt_tokens
            continue

        llm_response = response.choices[0].message.content
        llm_resp_dict = parse_json(llm_response)

        if not llm_resp_dict:
            continue

        with open(save_to, "a", encoding="utf8") as dest:
            dest.write(json.dumps({
                "id": ix,
                "story": story['content'].strip(),

                "output_scheme": json.dumps( TranslatedStory.model_json_schema(), ensure_ascii=False ),
                "task": f"You have to translate the story content into {targeted_lang} associated with a title into a JSON.",

                "response": llm_resp_dict,
            }, ensure_ascii=False, default=str)  + "\n" )

        ix += 1
        prompt_tokens += response.usage.prompt_tokens
        completion_tokens += response.usage.completion_tokens

        if(ix % 3) == 0:
            cost_input = (prompt_tokens / 1_000_000) * price_per_1m_input_tokens
            cost_output = (completion_tokens / 1_000_000) * price_per_1m_output_tokens
            total_cost = cost_input + cost_output

            print(f"Iteration {ix}: Total Cost = ${total_cost:.4f} ")

## Format Finetuning Datasets

In [20]:
sft_data_path = join(data_dir, "datasets", "sft.jsonl")
llm_finetunning_data = []

system_message = "\n".join([
    "You are a professional NLP data parser.",
    "Follow the provided `Task` by the user and the `Output Scheme` to generate the `Output JSON`.",
    "Do not generate any introduction or conclusion."
])

for line in open(sft_data_path):
    if line.strip() == "":
        continue

    rec = json.loads(line.strip())

    llm_finetunning_data.append({
        "system": system_message,
        "instruction": "\n".join([
            "# Story:",
            rec["story"],

            "# Task:",
            rec["task"],

            "# Output Scheme:",
            rec["output_scheme"],
            "",

            "# Output JSON:",
            "```json"

        ]),
        "input": "",
        "output": "\n".join([
            "```json",
            json.dumps(rec["response"], ensure_ascii=False, default=str),
            "```"
        ]),
        "history": []
    })

random.Random(101).shuffle(llm_finetunning_data)

In [21]:
len(llm_finetunning_data)

2766

In [25]:
rec

{'id': 2765,
 'story': 'عقد رئيس الوزراء الإثيوبي آبي أحمد اجتماعا بمشاركة الوزراء وكبار قادة الدولة تتعلق بسد النهضة من جهة، واتجاه المفاوضات المقبلة بشأنه من جهة ثانية، وذلك في ظل خلاف مستمر بين إثيوبيا ومصر حول تشغيل السد وملء خزانه. \n ويأتي الاجتماع الحكومي بعد يومين من تأكيد الحكومة الإثيوبية عدم التوصل لاتفاق نهائي خلال جولة المفاوضات الماضية في واشنطن بين وفود تمثل إثيوبيا ومصر والسودان برععاية وزارة الخزانة الأميركية. \n وكانت الخارجية المصرية أعلنت الخميس الماضي عن اتفاق نهائي أفضت إليه المفاوضات الأخيرة بواشنطن، بيد أن وزير المياه الإثيوبي سيليشي بقيلي ومسؤولين آخرين في حكومة بلاده أشاروا إلى إحراز تقدم دون التوصل لتسوية حاسمة. \n وكانت وزارة الخزانة الأميركية أعلنت -عقب الجولة الأخيرة من المفاوضات الثلاثية- أن واشنطن وافقت على تسهيل الاستعدادات لإبرام الاتفاق النهائي بشأن تشغيل وملء السد لعرضه على الوزراء والرؤساء بالدول المعنية للتوقيع عليه بحلول نهاية الشهر الجاري. \n  \n  \n  \n أشغال السدفي الأثناء، قال المهندس بلاتشو كاسا، نائب مدير مشروع سد النهضة الإثيوبي، للجزيرة إن

In [22]:
train_sample_sz = 2700

train_ds = llm_finetunning_data[:train_sample_sz]
eval_ds = llm_finetunning_data[train_sample_sz:]

os.makedirs(join(data_dir, "datasets", "llamafactory-finetune-data"), exist_ok=True)

with open(join(data_dir, "datasets", "llamafactory-finetune-data", "train.json"), "w") as dest:
    json.dump(train_ds, dest, ensure_ascii=False, default=str)

with open(join(data_dir, "datasets", "llamafactory-finetune-data", "val.json"), "w", encoding="utf8") as dest:
    json.dump(eval_ds, dest, ensure_ascii=False, default=str)

In [23]:
join(data_dir, "datasets", "llamafactory-finetune-data", "val.json")

'/gdrive/MyDrive/Colab_Notebooks/Finetuning/datasets/llamafactory-finetune-data/val.json'

## Finetuning


In [ ]:
# # Configure LLaMA-Factory for the new datasets

# # update /content/LLaMA-Factory/data/dataset_info.json and append
# ```
  "news_finetune_train": {
        "file_name": "/gdrive/MyDrive/Colab_Notebooks/Finetuning/datasets/llamafactory-finetune-data/train.json",
        "columns": {
            "prompt": "instruction",
            "query": "input",
            "response": "output",
            "system": "system",
            "history": "history"
        }
    },
  "news_finetune_val": {
        "file_name": "/gdrive/MyDrive/Colab_Notebooks/Finetuning/datasets/llamafactory-finetune-data/val.json",
        "columns": {
            "prompt": "instruction",
            "query": "input",
            "response": "output",
            "system": "system",
            "history": "history"
        }
    }
# ```


# https://wandb.ai/mr-bakrianoo/llamafactory/runs/apwbkni9
# https://wandb.ai/mr-bakrianoo/llamafactory/runs/c5tf0q90

In [24]:
%%writefile /content/LLaMA-Factory/examples/train_lora/news_finetune.yaml

### model
model_name_or_path: Qwen/Qwen2.5-1.5B-Instruct
trust_remote_code: true # trust

### method
stage: sft # super fine tuning
do_train: true
finetuning_type: lora
lora_rank: 64
lora_target: all

### dataset
dataset: news_finetune_train
eval_dataset: news_finetune_val
template: qwen # temp for each model
cutoff_len: 3500 # cuttoff for token
max_samples: 50 # optional for expereminting
overwrite_cache: true
preprocessing_num_workers: 16

### output
# resume_from_checkpoint: /gdrive/MyDrive/youtube-resources/llm-finetuning/models/checkpoint-1500
output_dir: /gdrive/MyDrive/Colab_Notebooks/Finetuning/models/sft # where to save the model
logging_steps: 10 # logging
save_steps: 500 # every 500 make a checkpoint to resume from it
plot_loss: true # for plotting the loss
# overwrite_output_dir: true

### train
per_device_train_batch_size: 1 # one sample in the batch
gradient_accumulation_steps: 4 # every 4 step calculate the loss - to fix the the per_device_train_batch_size
learning_rate: 1.0e-4
num_train_epochs: 3.0
lr_scheduler_type: cosine
warmup_ratio: 0.1 # for the first 10% don't change the learning rate
bf16: true # float 16 is good for memory
ddp_timeout: 180000000 # for model crash out

### eval
# val_size: 0.1
per_device_eval_batch_size: 1
eval_strategy: steps
eval_steps: 100

report_to: wandb
run_name: newsx-finetune-llamafactory

push_to_hub: true # push to hf
export_hub_model_id: "EbrahemHesham/news-analyzer"
hub_private_repo: true # private
hub_strategy: checkpoint # to upload every checkpoint

Writing /content/LLaMA-Factory/examples/train_lora/news_finetune.yaml


In [27]:
!cd LLaMA-Factory/ && llamafactory-cli train /content/LLaMA-Factory/examples/train_lora/news_finetune.yaml

2025-10-22 19:06:41.728621: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1761160001.749803    7434 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1761160001.756356    7434 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1761160001.772566    7434 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1761160001.772597    7434 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1761160001.772600    7434 computation_placer.cc:177] computation placer alr

## New Finetuned Model Evaluation

In [10]:
model = AutoModelForCausalLM.from_pretrained(
    base_model_id,
    device_map="auto",
    torch_dtype = dtype
)

tokenizer = AutoTokenizer.from_pretrained(base_model_id)

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


In [12]:
finetuned_model_id = "/gdrive/MyDrive/Colab_Notebooks/Finetuning/models/sft"
model.load_adapter(finetuned_model_id)

In [23]:
text = tokenizer.apply_chat_template(
    details_extraction_messages,
    tokenize=False,
    add_generation_prompt=True
)

model_inputs = tokenizer([text], return_tensors="pt").to(device) # run the tekonizer

generate_ids = model.generate(
    model_inputs.input_ids,
    max_new_tokens=200,
    do_sample=False, top_k=None, temperature=None, top_p=None # For sampling
)

generated_ids = [
    output_ids[len(input_ids):] # start from the start of the output ids
    for input_ids, output_ids in zip(model_inputs.input_ids, generate_ids)

]

response = tokenizer.batch_decode(generated_ids, skip_special_tokens=True)[0]


In [24]:
parse_json(response)

{'story_title': 'محمد صلاح: نجم مصر يتصدر قائمة أسرع لاعبين في دوري أبطال أوروبا',
 'story_keywords': ['محمد صلاح',
  'اليويفا',
  'دوري أبطال أوروبا',
  'ليفربول',
  'لويس أوبيندا'],
 'story_summary': ['محمد صلاح يتصدر قائمة أسرع لاعبين في دوري أبطال أوروبا.',
  'لويس أوبيندا يحتل المرتبة الأولى بسرعة 36.2 كم/ساعة.',
  'بيير إيمريك أوباميانج يحل ثانياً بـ 35.8 كم/ساعة.',
  'جيريمي فريمبونج يُحتل المركز الثالث بـ 35.6 كم/ساعة.'],
 'story_category': 'sports',
 'story_entities': [{}]}

In [26]:
# Evaluation for translation
text = tokenizer.apply_chat_template(
    translation_messages,
    tokenize=False,
    add_generation_prompt=True
)

model_inputs = tokenizer([text], return_tensors="pt").to(device) # run the tekonizer

generate_ids = model.generate(
    model_inputs.input_ids,
    max_new_tokens=200,
    do_sample=False, top_k=None, temperature=None, top_p=None # For sampling
)

generated_ids = [
    output_ids[len(input_ids):] # start from the start of the output ids
    for input_ids, output_ids in zip(model_inputs.input_ids, generate_ids)

]

response = tokenizer.batch_decode(generated_ids, skip_special_tokens=True)[0]


In [27]:
parse_json(response)

{'translated_title': 'Mohamed Salah Leads Speed Rankings in UEFA Champions League This Season',
 'translated_content': "Official statistics released by UEFA show that Egyptian star Mohamed Salah, who plays for Liverpool, entered the top 10 fastest players in this season's UEFA Champions League after registering a peak speed of 34.3 kilometers per hour.\n\nInter Milan ranked second with Luis Ospina at 36.2 km/h, followed by Cameroon player Pierre-Emerick Aubameyang from Monaco (35.8 km/h), while Dutch player Jerome Forte from Liverpool came third with a speed of 35.6 km/h.\n\nMohamed Salah faced a decline in his goal-scoring efficiency this season compared to previous years, which contributed to receiving criticism despite ranking first in Liverpool.\n\nThe statistics showed that Mohamed Salah was the fastest player in English Premier League during the UEFA Champions League tournament, ahead of Jerome Forte."}

## Cost Estimation

In [33]:
def generate_resp(messages):
    # Evaluation for translation
    text = tokenizer.apply_chat_template(
        messages,
        tokenize=False,
        add_generation_prompt=True
    )

    model_inputs = tokenizer([text], return_tensors="pt").to(device) # run the tekonizer

    generate_ids = model.generate(
        model_inputs.input_ids,
        max_new_tokens=200,
        do_sample=False, top_k=None, temperature=None, top_p=None # For sampling
    )

    generated_ids = [
        output_ids[len(input_ids):] # start from the start of the output ids
        for input_ids, output_ids in zip(model_inputs.input_ids, generate_ids)

    ]

    response= tokenizer.batch_decode(generated_ids, skip_special_tokens=True)[0]
    return  response

response = generate_resp(translation_messages)

In [30]:
from faker import Faker
fake = Faker('ar')
fake.text(max_nb_chars=random.randint(150, 200))

'بحث النفط الإكتفاء وقوعها فقامت مشارف التخطيط. ابتدعها الله وأزيز جديدة ولاتّساع باستخدام ببلا.'

In [34]:
from tqdm.auto import tqdm
from faker import Faker
import random
from datetime import datetime

start_time = datetime.now()
fake = Faker('ar')

input_tokens = 0
output_tokens = 0

for i in tqdm(range(30)):
    prompt = fake.text(max_nb_chars=random.randint(150, 200))

    messages = [
        {
            "role": "user",
            "content": prompt,
        }
    ]

    response = generate_resp(translation_messages)

    input_tokens += len(tokenizer.apply_chat_template(messages))
    output_tokens += len(tokenizer.encode(response)) # transform text to numbers

total_time = (datetime.now() - start_time).total_seconds()

print(f"Total Time: {total_time} seconds")
print(f"Input Tokens: {input_tokens}")
print(f"Output Tokens: {output_tokens}")
print(f"Total Tokens: {input_tokens + output_tokens}")

  0%|          | 0/30 [00:00<?, ?it/s]

Total Time: 385.504547 seconds
Input Tokens: 2432
Output Tokens: 5970
Total Tokens: 8402


In [36]:
# Numbers of output tokens / Total time = numbers of tokens per seconds
5970 / 385

21.823376623376625

## vLLM

In [48]:
base_model_id = "Qwen/Qwen2.5-1.5B-Instruct"
adapter_model_id = "/gdrive/MyDrive/Colab_Notebooks/Finetuning/models/sft"
# nohup and & in the end to run the cell in the background
# vllm has different lora modules for different services
!nohup vllm serve "{base_model_id}" --dtype=half --gpu-memory-utilization 0.8 --max_lora_rank 64 --enable-lora --lora-modules news-lora="{adapter_model_id}" &


nohup: appending output to 'nohup.out'


In [59]:
!tail -n 30 nohup.out

INFO 10-23 14:14:16 model_runner.py:1562] Graph capturing finished in 35 secs, took 0.33 GiB
INFO 10-23 14:14:16 llm_engine.py:431] init engine (profile, create kv cache, warmup model) took 44.02 seconds
INFO 10-23 14:14:17 api_server.py:756] Using supplied chat template:
INFO 10-23 14:14:17 api_server.py:756] None
INFO 10-23 14:14:17 serving_models.py:174] Loaded new LoRA adapter: name 'news-lora', path '/gdrive/MyDrive/Colab_Notebooks/Finetuning/models/sft'
INFO 10-23 14:14:17 launcher.py:21] Available routes are:
INFO 10-23 14:14:17 launcher.py:29] Route: /openapi.json, Methods: HEAD, GET
INFO 10-23 14:14:17 launcher.py:29] Route: /docs, Methods: HEAD, GET
INFO 10-23 14:14:17 launcher.py:29] Route: /docs/oauth2-redirect, Methods: HEAD, GET
INFO 10-23 14:14:17 launcher.py:29] Route: /redoc, Methods: HEAD, GET
INFO 10-23 14:14:17 launcher.py:29] Route: /health, Methods: GET
INFO 10-23 14:14:17 launcher.py:29] Route: /ping, Methods: POST, GET
INFO 10-23 14:14:17 launcher.py:29] Route: 

### Inference

In [61]:
tokenizer = AutoTokenizer.from_pretrained(base_model_id)

# Evaluation for translation
prompt = tokenizer.apply_chat_template(
    translation_messages,
    tokenize=False,
    add_generation_prompt=True
)

In [62]:
vllm_model_id = "news-lora"

llm_response = requests.post("http://localhost:8000/v1/completions", json={
    "model": vllm_model_id,
    "prompt": prompt,
    "max_tokens": 1000,
    "temperature": 0.3
})


llm_response.json()

{'id': 'cmpl-b9165d362cc74c1f907bc69e935be8b8',
 'object': 'text_completion',
 'created': 1761228878,
 'model': 'news-lora',
 'choices': [{'index': 0,
   'text': '```json\n{"translated_title": "Mohamed Salah Surpassed 10 Fastest Players in UEFA Champions League This Season", "translated_content": "Official statistics released by UEFA (UEFA) show that Egyptian star Mohamed Salah, a midfielder for Liverpool, entered the top 10 fastest players in the UEFA Champions League this season after reaching a top speed of 34.3 kilometers per hour. Luis Ospina, a player from Juventus, led the list with a speed of 36.2 kilometers per hour, followed by Pierre-Emerick Aubameyang, a player from Paris Saint-Germain (PSG), with a speed of 35.8 kilometers per hour. Mohamed Salah suffered from a decline in his goal-scoring efficiency this season compared to previous years, despite leading the goalscorers\' charts for Liverpool. The statistics showed that Mohamed Salah was the fastest player in the English 

## Load Testing

In [44]:
!pip install locust

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.9/44.9 kB 3.7 MB/s eta 0:00:00
  Using cached setuptools-80.9.0-py3-none-any.whl.metadata (6.6 kB)
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.4/1.4 MB 61.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 71.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.0/115.0 kB 11.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 409.5/409.5 kB 34.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.6/59.6 kB 5.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.9/78.9 kB 7.4 MB/s eta 0:00:00
Using cached setuptools-80.9.0-py3-none-any.whl (1.2 MB)
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 264.7/264.7 kB 24.4 MB/s eta 0:00:00
  Attempting uninstall: setuptools
    Found existing installation: setuptools 75.2.0
    Uninstalling setuptools-75.2.0:
      Successfully uninstalled setuptools-75.2.0
ERROR: pip's dependency resolver does not currently take into account a

In [63]:
%%writefile locust_file.py


import random
import json
from locust import HttpUser, task, between, constant
from transformers import AutoTokenizer
from faker import Faker

fake = Faker('ar')

class CompletionLoadTest(HttpUser):
    wait_time = between(1, 3)

    @task
    def post_completion(self):
        model_id = "news-lora"
        prompt = fake.text(max_nb_chars=random.randint(150, 200))

        message = {
            "model": model_id,
            "prompt": prompt,
            "max_tokens": 512,
            "temperature": 0.3
        }

        llm_response = self.client.post("/v1/completions", json=message)

        if llm_response.status_code == 200:
            with open("./vllm_tokens.txt", "a") as dest:
                dest.write(json.dumps({
                    "prompt": prompt,
                    "response": llm_response.json()["choices"][0]["text"],
                }, ensure_ascii=False) + "\n")


Overwriting locust_file.py


In [64]:
!locust --headless -f locust_file.py --host=http://localhost:8000 -u 20 -r 1 -t "60s" --html=locust_results.html

[2025-10-23 14:15:08,919] be135f2fa4a4/INFO/locust.main: Starting Locust 2.42.0
[2025-10-23 14:15:08,920] be135f2fa4a4/INFO/locust.main: Run time limit set to 60 seconds
Type     Name  # reqs      # fails |    Avg     Min     Max    Med |   req/s  failures/s
--------||-------|-------------|-------|-------|-------|-------|--------|-----------
--------||-------|-------------|-------|-------|-------|-------|--------|-----------
         Aggregated       0     0(0.00%) |      0       0       0      0 |    0.00        0.00

[2025-10-23 14:15:08,921] be135f2fa4a4/INFO/locust.runners: Ramping to 20 users at a rate of 1.00 per second
Type     Name  # reqs      # fails |    Avg     Min     Max    Med |   req/s  failures/s
--------||-------|-------------|-------|-------|-------|-------|--------|-----------
--------||-------|-------------|-------|-------|-------|-------|--------|-----------
         Aggregated       0     0(0.00%) |      0       0       0      0 |    0.00        0.00

Type     Na

In [ ]:
# Switching to vllm
from openai import OpenAI

openai_client = OpenAI(
    api_key=userdata.get("OPENAI_API_KEY"),
    # base_url = "http://localhost:8000"
)

openai_model_id = "gpt-4o-mini"

In [68]:
vllm_tokens = [
    json.loads(line.strip())
    for line in open("./vllm_tokens.txt") if line.strip() != ""]

In [69]:
base_model_id = "Qwen/Qwen2.5-1.5B-Instruct"
tokenizer = AutoTokenizer.from_pretrained(base_model_id)

total_input_tokens = sum([ len(tokenizer.encode(rec['prompt'])) for rec in vllm_tokens ])
total_output_tokens = sum([ len(tokenizer.encode(rec['response'])) for rec in vllm_tokens ])

print(f"Total Input Tokens: {total_input_tokens}")
print(f"Total Output Tokens: {total_output_tokens}")

Total Input Tokens: 2866
Total Output Tokens: 26623


In [71]:
26623 / 60
# here we can see the difference on using vllm

443.71666666666664